# Baseline Activity Bandits

Compare the performance of exisiting algorithms for maximizing activity (sum of rewards), both in the oracle and non-oracle scenarios. 

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import numpy as np
import random 
import matplotlib.pyplot as plt
import json 
import argparse 
import sys

In [3]:
from rmab.simulator import RMABSimulator
from rmab.uc_whittle import UCWhittleBuggy, UCWhittle
from rmab.ucw_value import UCWhittle_value
from rmab.baselines import optimal_whittle, random_policy, WIQL
from rmab.fr_dynamics import get_all_transitions
from rmab.utils import get_save_path, delete_duplicate_results


In [4]:
is_jupyter = 'ipykernel' in sys.modules

In [5]:
if is_jupyter: 
    seed        = 42
    n_arms      = 8
    budget      = 3
    discount    = 0.9
    alpha       = 3 
    n_episodes  = 30
    episode_len = 20
    n_epochs    = 10
    save_name = 'hyperparameter'
    save_with_date = True 
else:
    parser = argparse.ArgumentParser()
    parser.add_argument('--n_arms',         '-N', help='num beneficiaries (arms)', type=int, default=8)
    parser.add_argument('--episode_len',    '-H', help='episode length', type=int, default=20)
    parser.add_argument('--n_episodes',     '-T', help='num episodes', type=int, default=30)
    parser.add_argument('--budget',         '-B', help='budget', type=int, default=3)
    parser.add_argument('--n_epochs',       '-E', help='number of epochs (num_repeats)', type=int, default=10)
    parser.add_argument('--discount',       '-d', help='discount factor', type=float, default=0.9)
    parser.add_argument('--alpha',          '-a', help='alpha: for conf radius', type=float, default=3)
    parser.add_argument('--seed',           '-s', help='random seed', type=int, default=42)
    parser.add_argument('--save_name',      '-n', help='save name', type=str, default='results')
    parser.add_argument('--use_date', action='store_true')

    args = parser.parse_args()

    n_arms      = args.n_arms
    budget      = args.budget
    discount    = args.discount
    alpha       = args.alpha 
    seed        = args.seed
    n_episodes  = args.n_episodes
    episode_len = args.episode_len
    n_epochs    = args.n_epochs
    save_name   = args.save_name 
    save_with_date = args.use_date 



In [6]:
n_states = 2
n_actions = 2

In [7]:
all_population_size = 100 # number of random arms to generate
all_transitions = get_all_transitions(all_population_size)

In [8]:
all_transitions.shape

(100, 2, 2, 2)

In [9]:
all_features = np.arange(all_population_size)

In [10]:
np.random.seed(seed)
random.seed(seed)
simulator = RMABSimulator(all_population_size, all_features, all_transitions,
            n_arms, episode_len, n_epochs, n_episodes, budget, number_states=n_states)

acting should always be good! 0.000 < 0.044
acting should always be good! 0.000 < 0.162
acting should always be good! 0.108 < 0.183
good start state should always be good! 0.380 < 0.508
good start state should always be good! 0.506 < 0.760
cohort [83 53 70 45 44 39 22 80]
cohort [45 80  5 29 78 35 86 14]
cohort [42 28 84 76 68 46 97 15]
cohort [51 29 14 74 15  3 31 87]
cohort [55  0 94  4 72 26 38  3]
cohort [69 66 55 63 30 61 42 29]
cohort [83 68 66 27 99 32 35 23]
cohort [31  1 98 11 36  4 84 58]
cohort [ 5 41 86 49 97 13 58 42]
cohort [22 71 78 83 30 48 34 29]


In [11]:
np.random.seed(seed)
random.seed(seed)
random_rewards = random_policy(simulator, n_episodes, n_epochs)

first state [0 1 1 1 1 1 1 1]
instance 0, ep 1, state [0 0 0 1 1 1 0 1]
instance 0, ep 2, state [0 1 1 1 0 0 0 1]
instance 0, ep 3, state [0 0 0 1 0 1 1 0]
instance 0, ep 4, state [1 1 0 1 1 1 1 1]
instance 0, ep 5, state [0 0 0 0 0 1 0 0]
instance 0, ep 6, state [0 1 0 1 0 0 0 0]
instance 0, ep 7, state [1 0 1 0 0 0 0 1]
instance 0, ep 8, state [0 0 0 0 1 1 0 1]
instance 0, ep 9, state [0 1 0 0 0 1 1 1]
instance 0, ep 10, state [0 1 1 0 0 0 1 0]
instance 0, ep 11, state [1 0 1 1 0 1 1 1]
instance 0, ep 12, state [0 0 1 1 0 0 1 0]
instance 0, ep 13, state [1 1 1 1 0 1 1 0]
instance 0, ep 14, state [0 1 1 0 1 1 1 1]
instance 0, ep 15, state [0 0 1 1 1 0 1 1]
instance 0, ep 16, state [1 1 1 1 0 1 1 0]
instance 0, ep 17, state [0 0 0 1 0 0 0 0]
instance 0, ep 18, state [0 1 1 0 1 1 1 0]
instance 0, ep 19, state [1 1 0 1 0 0 1 1]
instance 0, ep 20, state [1 0 0 1 1 0 1 0]
instance 0, ep 21, state [0 1 1 1 0 1 1 1]
instance 0, ep 22, state [0 0 0 0 0 0 0 1]
instance 0, ep 23, state [1 0 0 1

In [12]:
np.random.seed(seed)
random.seed(seed)
optimal_reward = optimal_whittle(simulator, n_episodes, n_epochs, discount)

first state [0 1 1 1 1 1 1 1]
   state [0 1 1 1 1 1 1 1] state_WI [  0.39   0.47   0.47   0.26   0.45 -10.   -10.   -10.  ] sorted [2 1 4]
   state [0 1 1 0 1 0 1 1] state_WI [  0.39   0.47   0.47   0.71   0.45   0.52 -10.   -10.  ] sorted [3 5 2]
   state [0 1 1 1 1 1 0 0] state_WI [  0.39   0.47   0.47   0.26   0.45 -10.     0.49   0.82] sorted [7 6 2]
   state [0 1 1 1 0 0 0 0] state_WI [0.39 0.47 0.47 0.26 0.45 0.52 0.49 0.82] sorted [7 5 6]
   state [0 1 1 0 0 1 0 1] state_WI [  0.39   0.47   0.47   0.71   0.45 -10.     0.49 -10.  ] sorted [3 6 2]
   state [1 0 1 1 0 0 1 0] state_WI [  0.26   0.54   0.47   0.26   0.45   0.52 -10.     0.82] sorted [7 1 5]
   state [0 1 0 0 0 1 1 0] state_WI [  0.39   0.47   0.58   0.71   0.45 -10.   -10.     0.82] sorted [7 3 2]
   state [1 0 0 1 0 1 0 1] state_WI [  0.26   0.54   0.58   0.26   0.45 -10.     0.49 -10.  ] sorted [2 1 6]
   state [0 1 1 1 0 0 1 1] state_WI [  0.39   0.47   0.47   0.26   0.45   0.52 -10.   -10.  ] sorted [5 2 1]
   st

In [13]:
np.random.seed(seed)
random.seed(seed)
wiql_rewards = WIQL(simulator, n_episodes, n_epochs)

first state [0 1 1 1 1 1 1 1]
instance 0, ep 1, state [0 0 0 1 1 1 0 1]
instance 0, ep 2, state [0 1 1 1 0 0 0 1]
instance 0, ep 3, state [0 0 0 1 0 1 1 0]
instance 0, ep 4, state [1 1 0 1 1 1 1 1]
instance 0, ep 5, state [0 0 0 0 0 1 0 0]
instance 0, ep 6, state [0 1 0 1 0 0 0 0]
instance 0, ep 7, state [1 0 1 0 0 0 0 1]
instance 0, ep 8, state [0 0 0 0 1 1 0 1]
instance 0, ep 9, state [0 1 0 0 0 1 1 1]
instance 0, ep 10, state [0 1 1 0 0 0 1 0]
instance 0, ep 11, state [1 0 1 1 0 1 1 1]
instance 0, ep 12, state [0 0 1 1 0 0 1 0]
instance 0, ep 13, state [1 1 1 1 0 1 1 0]
instance 0, ep 14, state [0 1 1 0 1 1 1 1]
instance 0, ep 15, state [0 0 1 1 1 0 1 1]
instance 0, ep 16, state [1 1 1 1 0 1 1 0]
instance 0, ep 17, state [0 0 0 1 0 0 0 0]
instance 0, ep 18, state [0 1 1 0 1 1 1 0]
instance 0, ep 19, state [1 1 0 1 0 0 1 1]
instance 0, ep 20, state [1 0 0 1 1 0 1 0]
instance 0, ep 21, state [0 1 1 1 0 1 1 1]
instance 0, ep 22, state [0 0 0 0 0 0 0 1]
instance 0, ep 23, state [1 0 0 1

In [14]:
np.random.seed(seed)
random.seed(seed)
ucw_extreme_rewards = UCWhittleBuggy(simulator, n_episodes, n_epochs, discount, alpha=alpha, method='extreme')

solving UCWhittle using method: extreme
first state [0 1 1 1 1 1 1 1]
---------------------------------------------------
0 0  | a  [0 0 0 0 0 1 1 1]  | s'  [0 0 1 0 0 1 0 1]  | r  7    | WI  [0.898 0.9   0.9   0.9   0.9   0.9   0.9   0.9  ]
instance 0, ep 1, state [0 0 0 1 1 1 0 1]
instance 0, ep 2, state [0 1 1 1 0 0 0 1]
instance 0, ep 3, state [0 0 0 1 0 1 1 0]
instance 0, ep 4, state [1 1 0 1 1 1 1 1]
instance 0, ep 5, state [0 0 0 0 0 1 0 0]
---------------------------------------------------
0 100  | a  [0 0 0 0 0 1 1 1]  | s'  [0 0 0 0 0 1 0 0]  | r  1    | WI  [0.898 0.898 0.898 0.898 0.898 0.9   0.898 0.898]
instance 0, ep 6, state [0 1 0 1 0 0 0 0]
instance 0, ep 7, state [1 0 1 0 0 0 0 1]
instance 0, ep 8, state [0 0 0 0 1 1 0 1]
instance 0, ep 9, state [0 1 0 0 0 1 1 1]
instance 0, ep 10, state [0 1 1 0 0 0 1 0]
---------------------------------------------------
0 200  | a  [0 1 1 0 0 0 1 0]  | s'  [0 1 1 0 1 0 0 1]  | r  3    | WI  [0.898 0.9   0.9   0.898 0.898 0.898 0.

In [16]:
np.random.seed(seed)
random.seed(seed)
ucw_ucb_rewards = UCWhittleBuggy(simulator, n_episodes, n_epochs, discount, alpha=alpha, method='UCB')

solving UCWhittle using method: UCB
first state [0 1 1 1 1 1 1 1]
---------------------------------------------------
0 0  | a  [0 0 0 0 0 1 1 1]  | s'  [0 0 1 0 0 1 0 1]  | r  7    | WI  [-0. -0. -0. -0. -0. -0. -0. -0.]
instance 0, ep 1, state [0 0 0 1 1 1 0 1]
instance 0, ep 2, state [0 1 1 1 0 0 0 1]
instance 0, ep 3, state [0 0 0 1 0 1 1 0]
instance 0, ep 4, state [1 1 0 1 1 1 1 1]
instance 0, ep 5, state [0 0 0 0 0 1 0 0]
---------------------------------------------------
0 100  | a  [0 0 0 0 0 1 1 1]  | s'  [0 0 0 0 0 1 0 0]  | r  1    | WI  [-0. -0. -0. -0. -0. -0. -0. -0.]
instance 0, ep 6, state [0 1 0 1 0 0 0 0]
instance 0, ep 7, state [1 0 1 0 0 0 0 1]
instance 0, ep 8, state [0 0 0 0 1 1 0 1]
instance 0, ep 9, state [0 1 0 0 0 1 1 1]
instance 0, ep 10, state [0 1 1 0 0 0 1 0]
---------------------------------------------------
0 200  | a  [0 1 0 0 1 0 0 1]  | s'  [0 1 0 1 0 0 0 1]  | r  3    | WI  [-0.     0.017 -0.    -0.     0.01  -0.    -0.    -0.   ]
instance 0, ep 11

In [17]:
np.random.seed(seed)
random.seed(seed)
ucw_ucb_rewards_fixed = UCWhittle(simulator, n_episodes, n_epochs, discount, alpha=alpha, method='UCB',norm_confidence=False)

solving UCWhittle using method: UCB
first state [0 1 1 1 1 1 1 1]
---------------------------------------------------
0 0  | a  [0 0 0 0 0 1 1 1]  | s'  [0 0 1 0 0 1 0 1]  | r  7    | WI  [-0. -0. -0. -0. -0. -0. -0. -0.]
instance 0, ep 1, state [0 0 0 1 1 1 0 1]
instance 0, ep 2, state [0 1 1 1 0 0 0 1]
instance 0, ep 3, state [0 0 0 1 0 1 1 0]
instance 0, ep 4, state [1 1 0 1 1 1 1 1]
instance 0, ep 5, state [0 0 0 0 0 1 0 0]
---------------------------------------------------
0 100  | a  [0 0 0 0 0 1 1 1]  | s'  [0 0 0 0 0 1 0 0]  | r  1    | WI  [-0. -0. -0. -0. -0. -0. -0. -0.]
instance 0, ep 6, state [0 1 0 1 0 0 0 0]
instance 0, ep 7, state [1 0 1 0 0 0 0 1]
instance 0, ep 8, state [0 0 0 0 1 1 0 1]
instance 0, ep 9, state [0 1 0 0 0 1 1 1]
instance 0, ep 10, state [0 1 1 0 0 0 1 0]
---------------------------------------------------
0 200  | a  [0 0 0 0 0 1 1 1]  | s'  [1 1 1 0 0 1 1 0]  | r  3    | WI  [-0. -0. -0. -0. -0. -0. -0. -0.]
instance 0, ep 11, state [1 0 1 1 0 1 1 1

In [19]:
np.random.seed(seed)
random.seed(seed)
ucw_fixed_value_rewards = UCWhittle_value(simulator, n_episodes, n_epochs, discount, alpha=alpha)

solving UCWhittle using method: VALUE-BASED
first state [0 1 1 1 1 1 1 1]
--------------------------
Restricted license - for non-production use only - expires 2024-10-28


/usr0/home/naveenr/food_rescue_rmab/rmab/ucw_value.py:359: UserWarning: Uh oh! Model is not optimal; status is 11
  warnings.warn(f'Uh oh! Model is not optimal; status is {model.status}')


      arm 0 state 0, opt val 7.21, opt p [0.576 0.576 0.889 0.889]
      arm 0 state 1, opt val 8.85, opt p [0.407 0.407 0.932 0.932]
      arm 1 state 0, opt val 7.21, opt p [0. 0. 0. 0.]
      arm 1 state 1, opt val 8.85, opt p [0. 0. 0. 0.]
      arm 2 state 0, opt val 7.21, opt p [0. 0. 0. 0.]
      arm 2 state 1, opt val 8.85, opt p [0. 0. 0. 0.]
      arm 3 state 0, opt val 7.21, opt p [0. 0. 0. 0.]
      arm 3 state 1, opt val 8.85, opt p [0. 0. 0. 0.]
      arm 4 state 0, opt val 7.21, opt p [0. 0. 0. 0.]
      arm 4 state 1, opt val 8.85, opt p [0. 0. 0. 0.]
      arm 5 state 0, opt val 7.21, opt p [0. 0. 0. 0.]
      arm 5 state 1, opt val 8.85, opt p [0. 0. 0. 0.]
      arm 6 state 0, opt val 7.21, opt p [0. 0. 0. 0.]
      arm 6 state 1, opt val 8.85, opt p [0. 0. 0. 0.]
      arm 7 state 0, opt val 7.21, opt p [0. 0. 0. 0.]
      arm 7 state 1, opt val 8.85, opt p [0. 0. 0. 0.]
--------------------------
      arm 0 state 0, opt val 0.00, opt p [-0. -0. -0.  0.]
      arm 

/usr0/home/naveenr/food_rescue_rmab/rmab/ucw_value.py:359: UserWarning: Uh oh! Model is not optimal; status is 7
  warnings.warn(f'Uh oh! Model is not optimal; status is {model.status}')


can't get subsidy value. model status is 7
  state 1, lcb = [-0.    -0.    -0.     0.291], ucb = [1. 1. 1. 1.]
can't get p values. model status is 7
  state 1, lcb = [-0.    -0.    -0.     0.291], ucb = [1. 1. 1. 1.]
      arm 7 state 1, opt val -1.00, opt p [0.5   0.5   0.5   0.646]
--------------------------
      arm 0 state 0, opt val 0.00, opt p [-0. -0. -0.  0.]
      arm 0 state 1, opt val 1.00, opt p [-0. -0. -0.  0.]
      arm 1 state 0, opt val 0.00, opt p [-0. -0. -0.  0.]
      arm 1 state 1, opt val 1.00, opt p [-0. -0. -0.  0.]
      arm 2 state 0, opt val 0.00, opt p [0. 0. 0. 0.]
      arm 2 state 1, opt val 1.00, opt p [0. 0. 0. 0.]
      arm 3 state 0, opt val 0.00, opt p [0. 0. 0. 0.]
      arm 3 state 1, opt val 1.00, opt p [0. 0. 0. 0.]
      arm 4 state 0, opt val 0.00, opt p [-0. -0. -0.  0.]
      arm 4 state 1, opt val 1.00, opt p [-0. -0. -0.  0.]
      arm 5 state 0, opt val 0.00, opt p [0. 0. 0. 0.]
      arm 5 state 1, opt val 1.00, opt p [0. 0. 0. 0.]
    

In [20]:
mean_rewards = {'random_rewards': np.mean(random_rewards), 
 'optimal_rewards': np.mean(optimal_reward), 
 'wiql_rewards': np.mean(wiql_rewards), 
 'extreme_rewards': np.mean(ucw_extreme_rewards), 
 'ucb_rewards': np.mean(ucw_ucb_rewards), 
 'ucb_fixed_rewards': np.mean(ucw_ucb_rewards_fixed), 
 'value_fixed_rewards': np.mean(ucw_fixed_value_rewards)}
mean_rewards

{'random_rewards': 3.1005,
 'optimal_rewards': 3.5778333333333334,
 'wiql_rewards': 3.048,
 'extreme_rewards': 3.0008333333333335,
 'ucb_rewards': 2.8993333333333333,
 'ucb_fixed_rewards': 3.2001666666666666,
 'value_fixed_rewards': 3.025956738768719}

In [21]:
std_rewards = {'random_rewards': np.std(random_rewards), 
 'optimal_rewards': np.std(optimal_reward), 
 'wiql_rewards': np.std(wiql_rewards), 
 'extreme_rewards': np.std(ucw_extreme_rewards), 
 'ucb_rewards': np.std(ucw_ucb_rewards), 
 'ucb_fixed_rewards': np.std(ucw_ucb_rewards_fixed), 
 'value_fixed_rewards': np.std(ucw_fixed_value_rewards)}

In [22]:
random_match = 1-np.sum(random_rewards == 0)/random_rewards.size
optimal_match = 1-np.sum(optimal_reward == 0)/optimal_reward.size 
wiql_match = 1-np.sum(wiql_rewards == 0)/wiql_rewards.size 
ucw_extreme_match = 1-np.sum(ucw_extreme_rewards == 0)/ucw_extreme_rewards.size 
ucw_ucb_match = 1-np.sum(ucw_ucb_rewards == 0)/ucw_ucb_rewards.size
ucw_ucb_fixed_match = 1-np.sum(ucw_ucb_rewards_fixed == 0)/ucw_ucb_rewards_fixed.size 
ucw_fixed_value_match = 1-np.sum(ucw_fixed_value_rewards == 0)/ucw_fixed_value_rewards.size


In [23]:
match_rates = {
    'random_match': random_match, 
    'optimal_match': optimal_match, 
    'wiql_match': wiql_match, 
    'extreme_match': ucw_extreme_match, 
    'ucb_match': ucw_ucb_match, 
    'fixed_match': ucw_ucb_fixed_match, 
    'value_match': ucw_fixed_value_match, 
}
match_rates

{'random_match': 0.9846666666666667,
 'optimal_match': 0.996,
 'wiql_match': 0.9775,
 'extreme_match': 0.9875,
 'ucb_match': 0.9748333333333333,
 'fixed_match': 0.9836666666666667,
 'value_match': 0.9833610648918469}

In [24]:
data = {
    'mean_reward': mean_rewards, 
    'std_reward': std_rewards,
    'match_rate': match_rates, 
    'parameters': 
        {'seed'      : seed,
        'n_arms'    : n_arms,
        'budget'    : budget,
        'discount'  : discount, 
        'alpha'     : alpha, 
        'n_episodes': n_episodes, 
        'episode_len': episode_len, 
        'n_epochs'  : n_epochs} 
}

In [25]:
save_path = get_save_path('baseline',save_name,seed,use_date=save_with_date)

In [ ]:
delete_duplicate_results('baseline',save_name,data)

In [64]:
json.dump(data,open('../results/'+save_path,'w'))